In [1]:
%load_ext rpy2.ipython

In [2]:
%%R
set.seed(88888888) # maximum luck

library(DESeq2)
library(plotly)
library(ggplot2)
library(viridis)
library(magrittr)
library(pheatmap)
library(DescTools)
library(pdfCluster)
library(RColorBrewer)
library(SummarizedExperiment)
library(caret)
library(class)
library(htmlwidgets)

Loading required package: S4Vectors
Loading required package: stats4
Loading required package: BiocGenerics

Attaching package: ‘BiocGenerics’

The following objects are masked from ‘package:stats’:

    IQR, mad, sd, var, xtabs

The following objects are masked from ‘package:base’:

    anyDuplicated, aperm, append, as.data.frame, basename, cbind,
    colnames, dirname, do.call, duplicated, eval, evalq, Filter, Find,
    get, grep, grepl, intersect, is.unsorted, lapply, Map, mapply,
    match, mget, order, paste, pmax, pmax.int, pmin, pmin.int,
    Position, rank, rbind, Reduce, rownames, sapply, setdiff, sort,
    table, tapply, union, unique, unsplit, which.max, which.min


Attaching package: ‘S4Vectors’

The following object is masked from ‘package:utils’:

    findMatches

The following objects are masked from ‘package:base’:

    expand.grid, I, unname

Loading required package: IRanges
Loading required package: GenomicRanges
Loading required package: GenomeInfoDb
Loading require

In [3]:
%%R
OUT_DIR <- "/mnt/home/yuankeji/RanceLab/reticula_new/reticula/data/tcdd/output/"
N_FOLDS <- 10

In [4]:
%%R
vst.counts <- readRDS(paste(OUT_DIR, "vst_counts10vs0_time_course.Rds", sep = ""))
print(vst.counts)

class: DESeqTransform 
dim: 9297 90 
metadata(1): version
assays(1): ''
rownames(9297): ENSMUSG00000000001 ENSMUSG00000000028 ...
  ENSMUSG00000118462 ENSMUSG00000118541
rowData names(4): baseMean baseVar allZero dispFit
colnames(90): SRR7817611 SRR7817612 ... SRR4317653 SRR4317654
colData names(3): Sample Dose sizeFactor


In [5]:
%%R
sample <- colData(vst.counts)
# print(sample)

In [6]:
%%R
vst.count.mtx <-
   vst.counts %>% SummarizedExperiment::assay() %>% as.data.frame()
print(length(vst.count.mtx))
 head(vst.count.mtx)

[1] 90
                   SRR7817611 SRR7817612 SRR7817614 SRR7817615 SRR7817616
ENSMUSG00000000001  15.659179  15.694988  15.637947  15.713182  15.686606
ENSMUSG00000000028   9.823786   9.688285   9.933189   9.780866   9.849712
ENSMUSG00000000049  19.778895  19.774096  20.030675  19.999783  20.002420
ENSMUSG00000000058  10.414731  10.561287  10.594731  10.312029  10.838936
ENSMUSG00000000085  12.142421  11.913016  12.065779  12.065737  11.711334
ENSMUSG00000000088  16.629157  16.650663  16.621987  16.343977  16.299495
                   SRR7817623 SRR7817624 SRR7817625 SRR7817626 SRR7817627
ENSMUSG00000000001   15.61345  15.637252  15.773239  15.746706   15.57917
ENSMUSG00000000028   10.00687   9.819909   9.713758   9.874469   10.39372
ENSMUSG00000000049   20.01593  19.986000  19.917134  19.923143   19.94199
ENSMUSG00000000058   10.57930  10.937465  10.347793  10.512337   10.47006
ENSMUSG00000000085   11.87371  12.136689  12.228050  12.068366   11.75789
ENSMUSG00000000088   16.25383  

ENSMUSG00000000085   12.10584   11.96027  11.887187   12.09058   11.81074
ENSMUSG00000000088   16.16394   15.80464  15.764133   15.12028   15.45275
                   SRR4317607 SRR4317609 SRR4317610 SRR4317611 SRR4317612
ENSMUSG00000000001  15.047746   15.29209   15.40048   15.23869  15.121475
ENSMUSG00000000028   9.982948   10.25603   10.07307   10.34568   9.999054
ENSMUSG00000000049  20.140910   20.20441   20.21669   20.20371  20.201832
ENSMUSG00000000058  11.003789   11.14492   11.37852   10.95163  11.252063
ENSMUSG00000000085  12.207890   11.51409   11.87975   12.41048  11.696165
ENSMUSG00000000088  15.139023   14.84269   15.01859   14.89798  14.802793
                   SRR4317649 SRR4317651 SRR4317652 SRR4317653 SRR4317654
ENSMUSG00000000001  15.400038   15.50355   15.44196   15.72994   15.69150
ENSMUSG00000000028   9.924631   10.37974   10.24610   10.29100   10.21732
ENSMUSG00000000049  19.647805   18.93738   18.92325   19.20167   19.20616
ENSMUSG00000000058  11.570927   11.788

In [7]:
%%R
tcdd_dose_detail.vec <-
   readRDS(paste(OUT_DIR, "tcdd_dose_detail_vec10vs0_time_course.Rds", sep = ""))
print(tcdd_dose_detail.vec)

 [1]  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
[26]  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
[51]  0  0  0  0  0  0  0 10 10 10 10 10 10 10 10 10 10  0  0  0  0  0 10 10 10
[76] 10 10 10  0 10  0  0  0  0  0 10 10 10 10 10


In [8]:
%%R
rxn2ensembls.nls <-
   readRDS(paste(OUT_DIR, "rxn2ensembls_nls10vs0_time_course.Rds", sep = ""))
print(length(rxn2ensembls.nls))
print(rxn2ensembls.nls)

[1] 9825
$`R-MMU-170666`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSMUSG00000057614"

$`R-MMU-170671`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSMUSG00000057614"

$`R-MMU-170674`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSM

 [46] "ENSMUSG00000028777" "ENSMUSG00000028950" "ENSMUSG00000028971"
 [49] "ENSMUSG00000029064" "ENSMUSG00000029072" "ENSMUSG00000029236"
 [52] "ENSMUSG00000029371" "ENSMUSG00000029372" "ENSMUSG00000029373"
 [55] "ENSMUSG00000029379" "ENSMUSG00000029380" "ENSMUSG00000029417"
 [58] "ENSMUSG00000029530" "ENSMUSG00000029663" "ENSMUSG00000029713"
 [61] "ENSMUSG00000029819" "ENSMUSG00000031778" "ENSMUSG00000031861"
 [64] "ENSMUSG00000031980" "ENSMUSG00000032192" "ENSMUSG00000032562"
 [67] "ENSMUSG00000032766" "ENSMUSG00000033717" "ENSMUSG00000034117"
 [70] "ENSMUSG00000034855" "ENSMUSG00000035042" "ENSMUSG00000035383"
 [73] "ENSMUSG00000035431" "ENSMUSG00000035448" "ENSMUSG00000036353"
 [76] "ENSMUSG00000036362" "ENSMUSG00000036381" "ENSMUSG00000036402"
 [79] "ENSMUSG00000036437" "ENSMUSG00000036832" "ENSMUSG00000037010"
 [82] "ENSMUSG00000037014" "ENSMUSG00000037140" "ENSMUSG00000037346"
 [85] "ENSMUSG00000037944" "ENSMUSG00000038607" "ENSMUSG00000038668"
 [88] "ENSMUSG00000038811" "ENSMUS

 [4] "ENSMUSG00000019775" "ENSMUSG00000020599" "ENSMUSG00000021219"
 [7] "ENSMUSG00000024186" "ENSMUSG00000026357" "ENSMUSG00000026358"
[10] "ENSMUSG00000026475" "ENSMUSG00000026527" "ENSMUSG00000026678"
[13] "ENSMUSG00000028777" "ENSMUSG00000029101" "ENSMUSG00000032562"
[16] "ENSMUSG00000038530" "ENSMUSG00000042671" "ENSMUSG00000051079"
[19] "ENSMUSG00000052087" "ENSMUSG00000057614" "ENSMUSG00000059810"

$`R-MMU-8982019`
 [1] "ENSMUSG00000000001" "ENSMUSG00000002458" "ENSMUSG00000002459"
 [4] "ENSMUSG00000019775" "ENSMUSG00000020599" "ENSMUSG00000021219"
 [7] "ENSMUSG00000024186" "ENSMUSG00000026357" "ENSMUSG00000026358"
[10] "ENSMUSG00000026475" "ENSMUSG00000026527" "ENSMUSG00000026678"
[13] "ENSMUSG00000028777" "ENSMUSG00000029101" "ENSMUSG00000032562"
[16] "ENSMUSG00000038530" "ENSMUSG00000042671" "ENSMUSG00000051079"
[19] "ENSMUSG00000052087" "ENSMUSG00000057614" "ENSMUSG00000059810"

$`R-MMU-8982020`
 [1] "ENSMUSG00000000001" "ENSMUSG00000002458" "ENSMUSG00000002459"
 [4] "ENSMUS

 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000024325" "ENSMUSG00000025577" "ENSMUSG00000025578"
 [7] "ENSMUSG00000026021" "ENSMUSG00000026484" "ENSMUSG00000026739"
[10] "ENSMUSG00000028796" "ENSMUSG00000037652" "ENSMUSG00000039989"
[13] "ENSMUSG00000040669"

$`R-MMU-4570463`
 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000020265" "ENSMUSG00000020738" "ENSMUSG00000024325"
 [7] "ENSMUSG00000025577" "ENSMUSG00000025578" "ENSMUSG00000026484"
[10] "ENSMUSG00000026739" "ENSMUSG00000028796" "ENSMUSG00000031347"
[13] "ENSMUSG00000037652" "ENSMUSG00000039989" "ENSMUSG00000040669"

$`R-MMU-4570499`
 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000020738" "ENSMUSG00000021546" "ENSMUSG00000024325"
 [7] "ENSMUSG00000025577" "ENSMUSG00000025578" "ENSMUSG00000026484"
[10] "ENSMUSG00000026739" "ENSMUSG00000028796" "ENSMUSG00000037652"
[13] "ENSMUSG00000039989" "ENSMUSG00000040669"

$`R-MM

 [1] "ENSMUSG00000000126" "ENSMUSG00000009900" "ENSMUSG00000010797"
 [4] "ENSMUSG00000012282" "ENSMUSG00000015957" "ENSMUSG00000018486"
 [7] "ENSMUSG00000021994" "ENSMUSG00000022382" "ENSMUSG00000022996"
[10] "ENSMUSG00000022997" "ENSMUSG00000026167" "ENSMUSG00000027840"
[13] "ENSMUSG00000028173" "ENSMUSG00000029671" "ENSMUSG00000030093"
[16] "ENSMUSG00000030170" "ENSMUSG00000033227" "ENSMUSG00000036856"
[19] "ENSMUSG00000036961"

$`R-MMU-3781943`
 [1] "ENSMUSG00000000126" "ENSMUSG00000009900" "ENSMUSG00000010797"
 [4] "ENSMUSG00000012282" "ENSMUSG00000015957" "ENSMUSG00000018486"
 [7] "ENSMUSG00000021994" "ENSMUSG00000022382" "ENSMUSG00000022996"
[10] "ENSMUSG00000022997" "ENSMUSG00000026167" "ENSMUSG00000027840"
[13] "ENSMUSG00000028173" "ENSMUSG00000029671" "ENSMUSG00000030093"
[16] "ENSMUSG00000030170" "ENSMUSG00000033227" "ENSMUSG00000036856"
[19] "ENSMUSG00000036961"

$`R-MMU-205328`
[1] "ENSMUSG00000000127" "ENSMUSG00000005672" "ENSMUSG00000019966"
[4] "ENSMUSG00000032113" "ENSM

...

[1] "ENSMUSG00000042903"

$`R-NUL-9617710`
[1] "ENSMUSG00000042903"

$`R-NUL-9617742`
[1] "ENSMUSG00000042903"

$`R-NUL-9617757`
[1] "ENSMUSG00000042903"

$`R-NUL-9617903`
[1] "ENSMUSG00000042903"

$`R-NUL-9617912`
[1] "ENSMUSG00000042903"

$`R-MMU-187246`
[1] "ENSMUSG00000043013" "ENSMUSG00000045518"

$`R-MMU-189119`
[1] "ENSMUSG00000043013" "ENSMUSG00000045518"

$`R-MMU-391942`
[1] "ENSMUSG00000043017"

$`R-MMU-9726949`
[1] "ENSMUSG00000043017"

$`R-MMU-1564169`
[1] "ENSMUSG00000043089" "ENSMUSG00000056174" "ENSMUSG00000068196"

$`R-MMU-1602473`
[1] "ENSMUSG00000043089"

$`R-MMU-389424`
[1] "ENSMUSG00000043102"

$`R-MMU-9014672`
[1] "ENSMUSG00000043241" "ENSMUSG00000058301"

$`R-MMU-9014678`
[1] "ENSMUSG00000043241" "ENSMUSG00000058301"

$`R-MMU-162873`
[1] "ENSMUSG00000043257"

$`R-MMU-8878914`
[1] "ENSMUSG00000043300"

$`R-MMU-8858270`
[1] "ENSMUSG00000043421"

$`R-MMU-5605262`
[1] "ENSMUSG00000043648"

$`R-MMU-444620`
[1] "ENSMUSG00000043659" "ENSMUSG00000073804"

$`R-MMU-9009950`

[1] "ENSMUSG00000047002"

$`R-MMU-437240`
[1] "ENSMUSG00000047139"

$`R-MMU-140355`
[1] "ENSMUSG00000047250"

$`R-MMU-140359`
[1] "ENSMUSG00000047250"

$`R-MMU-2314678`
[1] "ENSMUSG00000047250"

$`R-MMU-9677320`
[1] "ENSMUSG00000047250"

$`R-MMU-6803890`
[1] "ENSMUSG00000047281"

$`R-MMU-947531`
[1] "ENSMUSG00000047454"

$`R-MMU-5340195`
[1] "ENSMUSG00000047638"

$`R-MMU-6806674`
[1] "ENSMUSG00000047719"

$`R-MMU-190681`
[1] "ENSMUSG00000047797"

$`R-MMU-9846477`
[1] "ENSMUSG00000047878"

$`R-MMU-8850846`
[1] "ENSMUSG00000048120"

$`R-MMU-8850854`
[1] "ENSMUSG00000048120"

$`R-MMU-8954468`
[1] "ENSMUSG00000048142"

$`R-MMU-70542`
[1] "ENSMUSG00000048217"

$`R-MMU-6804402`
[1] "ENSMUSG00000048349" "ENSMUSG00000059552"

$`R-MMU-418172`
[1] "ENSMUSG00000048376" "ENSMUSG00000060216"

$`R-MMU-9708866`
[1] "ENSMUSG00000048376"

$`R-MMU-9006144`
[1] "ENSMUSG00000048482"

$`R-MMU-5336430`
[1] "ENSMUSG00000048497" "ENSMUSG00000061273"

$`R-MMU-5687126`
[1] "ENSMUSG00000048756"

$`R-MMU-9624527`

[1] "ENSMUSG00000053647"

$`R-MMU-8980228`
[1] "ENSMUSG00000053846"

$`R-MMU-6787533`
[1] "ENSMUSG00000053870"

$`R-MMU-4084989`
[1] "ENSMUSG00000053916"

$`R-MMU-9708104`
[1] "ENSMUSG00000053965"

$`R-MMU-5688294`
[1] "ENSMUSG00000054021" "ENSMUSG00000058927" "ENSMUSG00000063694"

$`R-MMU-8850797`
[1] "ENSMUSG00000054046"

$`R-MMU-444204`
[1] "ENSMUSG00000054200"

$`R-MMU-9842656`
[1] "ENSMUSG00000054204" "ENSMUSG00000055471" "ENSMUSG00000087247"

$`R-MMU-9011343`
[1] "ENSMUSG00000054256"

$`R-MMU-9816416`
[1] "ENSMUSG00000054272"

$`R-MMU-9820700`
[1] "ENSMUSG00000054272" "ENSMUSG00000055942" "ENSMUSG00000099216"
[4] "ENSMUSG00000110097"

$`R-MMU-1296035`
[1] "ENSMUSG00000054342"

$`R-MMU-9013021`
[1] "ENSMUSG00000054364" "ENSMUSG00000073433"

$`R-MMU-9690494`
[1] "ENSMUSG00000054364"

$`R-NUL-4649029`
[1] "ENSMUSG00000054452"

$`R-MMU-1482861`
[1] "ENSMUSG00000054469"

$`R-MMU-1482867`
[1] "ENSMUSG00000054469"

$`R-MMU-9663768`
[1] "ENSMUSG00000054477"

$`R-MMU-9749977`
[1] "ENSMUSG

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)




$`R-MMU-549368`
[1] "ENSMUSG00000068742"

$`R-MMU-2002401`
[1] "ENSMUSG00000068794"

$`R-MMU-1614654`
[1] "ENSMUSG00000069324" "ENSMUSG00000074768"

$`R-MMU-8862300`
[1] "ENSMUSG00000069516"

$`R-MMU-8862320`
[1] "ENSMUSG00000069516"

$`R-MMU-399978`
[1] "ENSMUSG00000069662"

$`R-MMU-844438`
[1] "ENSMUSG00000069830"

$`R-MMU-844447`
[1] "ENSMUSG00000069830"

$`R-MMU-879222`
[1] "ENSMUSG00000069830"

$`R-MMU-75823`
[1] "ENSMUSG00000070348"

$`R-MMU-8952399`
[1] "ENSMUSG00000070691"

$`R-MMU-176588`
[1] "ENSMUSG00000070811" "ENSMUSG00000078798"

$`R-MMU-176604`
[1] "ENSMUSG00000070811" "ENSMUSG00000078798"

$`R-MMU-888572`
[1] "ENSMUSG00000070880"

$`R-MMU-9007901`
[1] "ENSMUSG00000070942"

$`R-MMU-199216`
[1] "ENSMUSG00000071253"

$`R-MMU-3296304`
[1] "ENSMUSG00000071311"

$`R-MMU-391935`
[1] "ENSMUSG00000071489"

$`R-MMU-8956458`
[1] "ENSMUSG00000071573"

$`R-MMU-977389`
[1] "ENSMUSG00000071637"

$`R-MMU-351210`
[1] "ENSMUSG00000071708"

$`R-MMU-9012721`
[1] "ENSMUSG00000071711"

$`R-

In [9]:
%%R
rxns <- rxn2ensembls.nls %>% names()

In [10]:
%%R
rxn_knn_misclass_rate.nls <- list()
rxn_knn_ari.nls <- list()
rxn_knn_ecount.nls <- list()
rxn_pca.nls <- list()
count <- 0

In [11]:
%%R
toi_indices <- seq(1,length(tcdd_dose_detail.vec))
print(toi_indices)

 [1]  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25
[26] 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50
[51] 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75
[76] 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90


In [12]:
%%R
tcdd_dose_detail_vec_tis_of_interest <-
   tcdd_dose_detail.vec[toi_indices]
print(tcdd_dose_detail_vec_tis_of_interest)

 [1]  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
[26]  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
[51]  0  0  0  0  0  0  0 10 10 10 10 10 10 10 10 10 10  0  0  0  0  0 10 10 10
[76] 10 10 10  0 10  0  0  0  0  0 10 10 10 10 10


In [13]:
%%R
vst.count.mtx.tis_of_interest <- vst.count.mtx[, toi_indices]
print(vst.count.mtx.tis_of_interest)

                   SRR7817611 SRR7817612 SRR7817614 SRR7817615 SRR7817616
ENSMUSG00000000001  15.659179  15.694988  15.637947  15.713182  15.686606
ENSMUSG00000000028   9.823786   9.688285   9.933189   9.780866   9.849712
ENSMUSG00000000049  19.778895  19.774096  20.030675  19.999783  20.002420
ENSMUSG00000000058  10.414731  10.561287  10.594731  10.312029  10.838936
ENSMUSG00000000085  12.142421  11.913016  12.065779  12.065737  11.711334
ENSMUSG00000000088  16.629157  16.650663  16.621987  16.343977  16.299495
ENSMUSG00000000120  11.485476  11.559748  11.611084  11.224322  11.162465
ENSMUSG00000000126   9.592747   9.940820   9.475975   9.991542   9.841106
ENSMUSG00000000127  11.430954  11.250391  11.540619  11.441175  11.694287
ENSMUSG00000000142  11.608855  11.602313  11.583975  12.344672  12.096498
ENSMUSG00000000149  15.902798  15.985749  15.956886  16.063519  15.860769
ENSMUSG00000000154  15.416265  15.518723  15.592581  15.643789  15.655186
ENSMUSG00000000168  14.728282  14.7738

ENSMUSG00000001105  14.266803  14.290484  13.923741  13.969447  13.905391
ENSMUSG00000001119  11.509192  11.002296  11.238483  11.337321  11.808250
ENSMUSG00000001123  18.049687  18.048343  18.188848  18.229472  18.252264
ENSMUSG00000001127  15.139352  15.192111  15.362068  15.410931  15.505947
ENSMUSG00000001128  13.160253  13.303339  12.672380  12.920772  12.906900
ENSMUSG00000001131   9.037940   9.036766   8.558810   8.573322   9.505813
ENSMUSG00000001143  12.682840  12.526123  12.875950  12.861570  12.618965
ENSMUSG00000001155  18.474472  18.430509  18.560103  18.410666  18.374677
ENSMUSG00000001158  12.137513  11.964446  12.372009  11.965448  11.949236
ENSMUSG00000001173  11.289145  11.333790  11.778659  11.337321  11.717760
ENSMUSG00000001175  17.037651  17.074741  17.143185  17.224521  17.258424
ENSMUSG00000001211  16.767941  16.783563  16.787364  16.804305  16.765515
ENSMUSG00000001225   8.573322   9.032404   8.558810   8.573322   8.573199
ENSMUSG00000001228   9.663424   9.8394

ENSMUSG00000002249  12.253723  12.290086  12.412834  12.485691  12.225844
ENSMUSG00000002250  14.569189  14.710532  14.237152  14.887362  14.958425
ENSMUSG00000002257   9.432530   9.322436   9.379173   9.663424   9.593188
ENSMUSG00000002279  13.686157  14.073950  14.062587  14.244993  14.142576
ENSMUSG00000002289  13.277888  13.142214  14.323307  13.071516  13.292322
ENSMUSG00000002297  10.453145  10.603024  10.302640  10.237343  10.112159
ENSMUSG00000002307  12.425259  12.454916  12.498935  12.607329  12.604577
ENSMUSG00000002308  11.167338  11.148105  10.850886  11.390525  11.091947
ENSMUSG00000002324  10.332271  10.110198  10.729612   9.784329   9.989212
ENSMUSG00000002325  14.043934  14.144093  14.076708  14.381255  14.498311
ENSMUSG00000002326  12.665884  12.706129  12.472185  12.531934  12.636304
ENSMUSG00000002346  15.934728  15.982273  15.852089  15.902479  15.931275
ENSMUSG00000002365  14.084741  14.142323  14.413138  14.380319  14.435662
ENSMUSG00000002379  14.547830  14.3731

ENSMUSG00000003379   9.594196   9.776975   9.132090   9.594196   9.332201
ENSMUSG00000003402  15.968263  15.901057  15.996074  15.969876  15.865838
ENSMUSG00000003411   9.432530   9.715988   9.332166   9.663424   9.517134
ENSMUSG00000003418   8.573322   9.036766   9.132090   8.573322   9.037428
ENSMUSG00000003421  13.243466  13.454739  13.491699  13.398897  13.297119
ENSMUSG00000003429  14.839666  14.881566  14.604918  14.308168  14.393331
ENSMUSG00000003435  15.423552  15.414346  14.910638  15.256179  15.229709
ENSMUSG00000003436   8.573322   8.573040   8.558810   8.573322   8.573199
ENSMUSG00000003437  13.886097  13.748724  13.899162  13.691119  13.437724
ENSMUSG00000003444  10.990590  10.646316  11.099772  10.906957  11.213706
ENSMUSG00000003452   9.209908   9.205585   8.558810   8.573322   9.209251
ENSMUSG00000003458  14.303195  14.280325  14.147011  14.540828  14.488860
ENSMUSG00000003464  15.683687  15.823783  15.822322  15.874647  15.821814
ENSMUSG00000003476   9.332963   9.6609

ENSMUSG00000004654   8.573322   8.573040   8.558810   8.573322   8.573199
ENSMUSG00000004655  15.217483  15.228636  15.000947  15.211112  15.206762
ENSMUSG00000004665  11.466479  11.250014  11.189272  11.402715  11.712797
ENSMUSG00000004667  13.745563  13.922543  13.605584  13.476135  13.588173
ENSMUSG00000004668   8.573322   9.036766   8.558810   8.573322   8.573199
ENSMUSG00000004677  14.104814  14.125454  13.757623  13.898144  13.830796
ENSMUSG00000004709   9.037940   9.430579   9.132090   9.037940   9.500904
ENSMUSG00000004730  13.132806  13.191222  11.576899  12.671199  12.641869
ENSMUSG00000004768  12.014507  11.769633  12.044167  11.969798  11.997593
ENSMUSG00000004771  14.777237  14.901424  14.844031  14.797865  14.727817
ENSMUSG00000004788  13.119485  13.302713  12.992183  13.013738  13.041655
ENSMUSG00000004789  16.921985  16.952760  16.866286  16.903494  16.965348
ENSMUSG00000004791   9.037940   9.036766   8.558810   8.573322   8.573199
ENSMUSG00000004815  14.314102  14.2720

...

ENSMUSG00000006998  15.914853  16.254951  16.295355  16.174318  16.136660
ENSMUSG00000007033  10.349808  11.085484  11.278589  10.587749  10.626452
ENSMUSG00000007034   9.967262  10.483000  10.196168   9.925261   9.870842
ENSMUSG00000007038  15.095511  14.820891  14.835704  14.826784  14.858877
ENSMUSG00000007050  11.602643  11.716325  11.534953  11.307323  11.444243
ENSMUSG00000007080  10.697298  10.552945  10.695776  10.975658  10.871977
ENSMUSG00000007097  10.062960   9.797040   9.849063  10.171379  10.136603
ENSMUSG00000007107   9.208333   9.124409   8.897824   8.560981   8.560553
ENSMUSG00000007122   9.643792   9.452450   9.310627   9.563068   9.490116
ENSMUSG00000007207   9.597583   9.855906   9.437913   9.657543   9.787274
ENSMUSG00000007216  10.480666  10.422202  10.438403  10.713656  10.440597
ENSMUSG00000007279   8.553875   8.539897   8.539738   8.986484   8.560553
ENSMUSG00000007338  13.844689  13.787446  13.948708  13.472188  13.618077
ENSMUSG00000007379  10.081579  10.2896

ENSMUSG00000009907  14.596945  14.391169  14.443973  14.638706  14.475799
ENSMUSG00000009927  16.259177  16.538932  16.516191  15.883229  15.934606
ENSMUSG00000009941   9.105485   8.539897   8.539738   8.560981   8.560553
ENSMUSG00000009995  14.049834  13.769824  13.715992  13.745702  13.950666
ENSMUSG00000010021   9.296417   9.370395   9.497449   8.920763   8.984701
ENSMUSG00000010025  17.123397  17.701035  17.714042  17.340528  17.309025
ENSMUSG00000010045  13.037938  13.420229  13.346136  13.417621  13.331349
ENSMUSG00000010047  14.045083  13.833055  13.805692  14.128143  13.965115
ENSMUSG00000010051  14.379414  13.889034  13.760417  15.199901  15.152153
ENSMUSG00000010057  12.204234  12.169303  12.244864  11.898686  11.907210
ENSMUSG00000010064  19.001097  18.566685  18.556163  19.089271  19.107470
ENSMUSG00000010066   8.553875   8.898491   8.910686   8.986484   8.984701
ENSMUSG00000010095  15.427398  15.698141  15.703566  16.438639  16.396438
ENSMUSG00000010097  15.024275  14.7331

ENSMUSG00000014602   8.553875   9.265649   9.571906   9.430608   9.487510
ENSMUSG00000014606  14.759966  14.486115  14.508850  14.620001  14.671619
ENSMUSG00000014609   9.270496   9.027527   9.120042   8.560981   8.560553
ENSMUSG00000014704   9.434778   9.680239   9.647505   9.256391   9.759170
ENSMUSG00000014763  13.330401  13.573688  13.468129  13.637358  13.576350
ENSMUSG00000014767  13.252567  13.077277  13.135101  12.907035  13.112673
ENSMUSG00000014769  15.900530  15.732917  15.786553  15.609040  15.580731
ENSMUSG00000014773  10.974742  10.741793  11.107817  10.703323  10.771943
ENSMUSG00000014786   9.640120   9.851226   9.646850   9.421906   9.605054
ENSMUSG00000014850  12.604005  12.524025  12.669751  12.367988  12.640463
ENSMUSG00000014852  11.451285  11.195456  11.106423  11.434201  11.313022
ENSMUSG00000014859  12.477313  12.703301  12.700635  12.061495  11.924176
ENSMUSG00000014867  16.988217  17.089037  17.115611  16.782610  16.771486
ENSMUSG00000014932  13.880823  13.7747

ENSMUSG00000016256  16.914058  17.167005  17.213856  16.799629  16.797156
ENSMUSG00000016283   9.725682  10.321313   9.966104   9.921359   9.920163
ENSMUSG00000016308  13.045380  13.534472  13.424643  13.151731  13.124261
ENSMUSG00000016319  17.253517  17.705980  17.715851  17.329898  17.337898
ENSMUSG00000016327   8.553875   8.539897   8.539738   8.560981   8.560553
ENSMUSG00000016356   9.763052   9.869809   9.684025  10.023915   9.879777
ENSMUSG00000016409  12.060642  11.992053  12.170336  11.854260  11.725634
ENSMUSG00000016427  14.837969  14.842665  14.825082  14.249642  14.248930
ENSMUSG00000016477  12.391288  12.189458  12.151634  11.821160  12.092504
ENSMUSG00000016487  13.897639  14.212940  14.231855  14.258486  14.191332
ENSMUSG00000016493  11.608712  11.841353  11.677319  11.295510  11.053107
ENSMUSG00000016494  10.637017  10.884451  10.866614  10.666796  10.502052
ENSMUSG00000016496  11.715472  12.196093  12.282747  10.871620  11.079617
ENSMUSG00000016498   8.553875   9.0253

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [14]:
%%R
training_indices <-
   caret::createDataPartition(
      tcdd_dose_detail_vec_tis_of_interest,
      times = 1,
      p = 1.0, # no data will be held out when set to "1.0"
      list = FALSE
   )
print(training_indices)

      Resample1
 [1,]         1
 [2,]         2
 [3,]         3
 [4,]         4
 [5,]         5
 [6,]         6
 [7,]         7
 [8,]         8
 [9,]         9
[10,]        10
[11,]        11
[12,]        12
[13,]        13
[14,]        14
[15,]        15
[16,]        16
[17,]        17
[18,]        18
[19,]        19
[20,]        20
[21,]        21
[22,]        22
[23,]        23
[24,]        24
[25,]        25
[26,]        26
[27,]        27
[28,]        28
[29,]        29
[30,]        30
[31,]        31
[32,]        32
[33,]        33
[34,]        34
[35,]        35
[36,]        36
[37,]        37
[38,]        38
[39,]        39
[40,]        40
[41,]        41
[42,]        42
[43,]        43
[44,]        44
[45,]        45
[46,]        46
[47,]        47
[48,]        48
[49,]        49
[50,]        50
[51,]        51
[52,]        52
[53,]        53
[54,]        54
[55,]        55
[56,]        56
[57,]        57
[58,]        58
[59,]        59
[60,]        60
[61,]        61
[62,]   

In [15]:
%%R
vst.count.mtx.train <-
   vst.count.mtx.tis_of_interest[, training_indices] #9/10ths of data
vst.count.mtx.test  <-
   vst.count.mtx.tis_of_interest[, -training_indices] #1/10th of data

print(vst.count.mtx.train)

                   SRR7817611 SRR7817612 SRR7817614 SRR7817615 SRR7817616
ENSMUSG00000000001  15.659179  15.694988  15.637947  15.713182  15.686606
ENSMUSG00000000028   9.823786   9.688285   9.933189   9.780866   9.849712
ENSMUSG00000000049  19.778895  19.774096  20.030675  19.999783  20.002420
ENSMUSG00000000058  10.414731  10.561287  10.594731  10.312029  10.838936
ENSMUSG00000000085  12.142421  11.913016  12.065779  12.065737  11.711334
ENSMUSG00000000088  16.629157  16.650663  16.621987  16.343977  16.299495
ENSMUSG00000000120  11.485476  11.559748  11.611084  11.224322  11.162465
ENSMUSG00000000126   9.592747   9.940820   9.475975   9.991542   9.841106
ENSMUSG00000000127  11.430954  11.250391  11.540619  11.441175  11.694287
ENSMUSG00000000142  11.608855  11.602313  11.583975  12.344672  12.096498
ENSMUSG00000000149  15.902798  15.985749  15.956886  16.063519  15.860769
ENSMUSG00000000154  15.416265  15.518723  15.592581  15.643789  15.655186
ENSMUSG00000000168  14.728282  14.7738

ENSMUSG00000001105  14.266803  14.290484  13.923741  13.969447  13.905391
ENSMUSG00000001119  11.509192  11.002296  11.238483  11.337321  11.808250
ENSMUSG00000001123  18.049687  18.048343  18.188848  18.229472  18.252264
ENSMUSG00000001127  15.139352  15.192111  15.362068  15.410931  15.505947
ENSMUSG00000001128  13.160253  13.303339  12.672380  12.920772  12.906900
ENSMUSG00000001131   9.037940   9.036766   8.558810   8.573322   9.505813
ENSMUSG00000001143  12.682840  12.526123  12.875950  12.861570  12.618965
ENSMUSG00000001155  18.474472  18.430509  18.560103  18.410666  18.374677
ENSMUSG00000001158  12.137513  11.964446  12.372009  11.965448  11.949236
ENSMUSG00000001173  11.289145  11.333790  11.778659  11.337321  11.717760
ENSMUSG00000001175  17.037651  17.074741  17.143185  17.224521  17.258424
ENSMUSG00000001211  16.767941  16.783563  16.787364  16.804305  16.765515
ENSMUSG00000001225   8.573322   9.032404   8.558810   8.573322   8.573199
ENSMUSG00000001228   9.663424   9.8394

ENSMUSG00000002249  12.253723  12.290086  12.412834  12.485691  12.225844
ENSMUSG00000002250  14.569189  14.710532  14.237152  14.887362  14.958425
ENSMUSG00000002257   9.432530   9.322436   9.379173   9.663424   9.593188
ENSMUSG00000002279  13.686157  14.073950  14.062587  14.244993  14.142576
ENSMUSG00000002289  13.277888  13.142214  14.323307  13.071516  13.292322
ENSMUSG00000002297  10.453145  10.603024  10.302640  10.237343  10.112159
ENSMUSG00000002307  12.425259  12.454916  12.498935  12.607329  12.604577
ENSMUSG00000002308  11.167338  11.148105  10.850886  11.390525  11.091947
ENSMUSG00000002324  10.332271  10.110198  10.729612   9.784329   9.989212
ENSMUSG00000002325  14.043934  14.144093  14.076708  14.381255  14.498311
ENSMUSG00000002326  12.665884  12.706129  12.472185  12.531934  12.636304
ENSMUSG00000002346  15.934728  15.982273  15.852089  15.902479  15.931275
ENSMUSG00000002365  14.084741  14.142323  14.413138  14.380319  14.435662
ENSMUSG00000002379  14.547830  14.3731

ENSMUSG00000003379   9.594196   9.776975   9.132090   9.594196   9.332201
ENSMUSG00000003402  15.968263  15.901057  15.996074  15.969876  15.865838
ENSMUSG00000003411   9.432530   9.715988   9.332166   9.663424   9.517134
ENSMUSG00000003418   8.573322   9.036766   9.132090   8.573322   9.037428
ENSMUSG00000003421  13.243466  13.454739  13.491699  13.398897  13.297119
ENSMUSG00000003429  14.839666  14.881566  14.604918  14.308168  14.393331
ENSMUSG00000003435  15.423552  15.414346  14.910638  15.256179  15.229709
ENSMUSG00000003436   8.573322   8.573040   8.558810   8.573322   8.573199
ENSMUSG00000003437  13.886097  13.748724  13.899162  13.691119  13.437724
ENSMUSG00000003444  10.990590  10.646316  11.099772  10.906957  11.213706
ENSMUSG00000003452   9.209908   9.205585   8.558810   8.573322   9.209251
ENSMUSG00000003458  14.303195  14.280325  14.147011  14.540828  14.488860
ENSMUSG00000003464  15.683687  15.823783  15.822322  15.874647  15.821814
ENSMUSG00000003476   9.332963   9.6609

ENSMUSG00000004654   8.573322   8.573040   8.558810   8.573322   8.573199
ENSMUSG00000004655  15.217483  15.228636  15.000947  15.211112  15.206762
ENSMUSG00000004665  11.466479  11.250014  11.189272  11.402715  11.712797
ENSMUSG00000004667  13.745563  13.922543  13.605584  13.476135  13.588173
ENSMUSG00000004668   8.573322   9.036766   8.558810   8.573322   8.573199
ENSMUSG00000004677  14.104814  14.125454  13.757623  13.898144  13.830796
ENSMUSG00000004709   9.037940   9.430579   9.132090   9.037940   9.500904
ENSMUSG00000004730  13.132806  13.191222  11.576899  12.671199  12.641869
ENSMUSG00000004768  12.014507  11.769633  12.044167  11.969798  11.997593
ENSMUSG00000004771  14.777237  14.901424  14.844031  14.797865  14.727817
ENSMUSG00000004788  13.119485  13.302713  12.992183  13.013738  13.041655
ENSMUSG00000004789  16.921985  16.952760  16.866286  16.903494  16.965348
ENSMUSG00000004791   9.037940   9.036766   8.558810   8.573322   8.573199
ENSMUSG00000004815  14.314102  14.2720

...


ENSMUSG00000006127  13.259277  12.935470  12.813014  12.799719  12.907111
ENSMUSG00000006134  13.841570  13.840554  13.776481  14.082843  14.163360
ENSMUSG00000006169  14.838273  15.041130  14.975409  15.127219  15.042904
ENSMUSG00000006205  10.117902  10.827851  10.739680  10.252814  10.028277
ENSMUSG00000006216   8.553875   8.539897   8.539738   8.560981   8.560553
ENSMUSG00000006219  10.154714  10.613835  10.989918  10.342661  10.452918
ENSMUSG00000006235  10.149295   9.825867   9.956353  10.064200  10.024077
ENSMUSG00000006262  14.956618  14.671763  14.727908  15.187940  15.199432
ENSMUSG00000006269   8.553875   8.539897   8.539738   8.560981   8.560553
ENSMUSG00000006273  14.531817  14.213156  14.236393  14.403867  14.225654
ENSMUSG00000006276  12.766606  12.481722  12.592012  12.818549  12.626295
ENSMUSG00000006288  11.743272  11.909305  11.851656  12.006667  11.898773
ENSMUSG00000006299  16.283551  15.766360  15.788991  16.004958  15.983676
ENSMUSG00000006301  15.160791  15.233

ENSMUSG00000007989  10.012508  10.291056  10.320067  10.042160   9.804076
ENSMUSG00000008035  12.865035  12.118137  12.291135  12.687025  12.436190
ENSMUSG00000008036  14.779671  14.592051  14.674570  14.371341  14.556543
ENSMUSG00000008090  13.302252  12.807571  12.821978  12.797514  12.905776
ENSMUSG00000008167  15.088596  14.828795  14.875515  14.988541  14.973172
ENSMUSG00000008206  11.343826  10.980611  11.134087  11.111207  11.079941
ENSMUSG00000008301  13.389546  13.148979  13.162524  12.927733  12.977835
ENSMUSG00000008305  13.920678  14.223328  14.182731  14.197838  14.102689
ENSMUSG00000008333  12.351932  12.275655  12.365814  12.039599  12.026374
ENSMUSG00000008348  18.895964  19.057249  19.086138  19.105344  19.064743
ENSMUSG00000008373  12.799099  12.902344  12.955902  12.694166  12.694470
ENSMUSG00000008435  12.341469  12.168856  12.201067  12.492041  12.207591
ENSMUSG00000008438   8.553875   8.539897   8.539738   9.248351   8.976718
ENSMUSG00000008461  10.861394  11.0309

ENSMUSG00000011179  14.228359  13.793434  13.813784  13.970222  14.122228
ENSMUSG00000011256  10.754199  10.683506  10.619133  10.651842  10.410046
ENSMUSG00000011306  12.890903  12.838856  12.681551  12.945687  13.168316
ENSMUSG00000011463   8.553875   8.539897   8.539738   8.560981   8.560553
ENSMUSG00000011658  12.848061  12.400554  12.178564  12.695399  12.419786
ENSMUSG00000011751   9.212122   8.539897   9.028831   9.254394   8.984701
ENSMUSG00000011752  12.727187  13.892534  13.812962  13.194368  13.194583
ENSMUSG00000011837  11.635058  11.433066  11.341295  11.234030  11.272560
ENSMUSG00000011877  12.273789  12.011002  12.226340  12.260435  11.995857
ENSMUSG00000011884  11.581136  11.500194  11.657537  11.289139  11.411791
ENSMUSG00000011958  14.421710  14.195429  14.266493  14.175032  14.207774
ENSMUSG00000011960  13.872873  14.461038  14.543868  14.191489  14.117410
ENSMUSG00000012114  13.457893  13.115819  13.230704  13.504335  13.631632
ENSMUSG00000012117  13.507881  13.7096

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



   8.560981   8.648685
ENSMUSG00000017733   8.553875   8.539897   8.539738   8.560981   8.560553
ENSMUSG00000017737  10.143303   9.606860   9.698316   9.555937   9.662792
ENSMUSG00000017740  10.374430  10.278110  10.383812  10.738573  10.551770
ENSMUSG00000017747  12.566949  12.703809  12.760115  12.544211  12.619808
ENSMUSG00000017754  14.173841  13.505775  13.565768  13.932447  14.063726
ENSMUSG00000017756  15.690399  14.905691  14.890303  15.287028  15.311993
ENSMUSG00000017760  16.696593  16.375212  16.415150  16.483930  16.557426
ENSMUSG00000017765  12.298599  11.518813  11.511829  12.128665  12.135410
ENSMUSG00000017774  14.486556  14.396395  14.360460  14.670006  14.757797
ENSMUSG00000017776  15.314598  15.423713  15.382923  15.422775  15.403892
ENSMUSG00000017778  16.622767  16.709424  16.736451  16.401518  16.383107
ENSMUSG00000017781  14.503805  14.301410  14.285294  14.238977  14.291878
ENSMUSG00000017831  14.575346  14.384304  14.446338  14.457288  14.536585
ENSMUSG00000017

In [16]:
%%R
tcdd_dose_detail.vec.train <-
   tcdd_dose_detail_vec_tis_of_interest[training_indices]
tcdd_dose_detail.vec.test <-
   tcdd_dose_detail_vec_tis_of_interest[-training_indices]

# print(gtex_tissue_detail.vec.train)
print(length(unique(tcdd_dose_detail.vec.train)))

[1] 2


In [17]:
%%R
saveRDS(tcdd_dose_detail.vec.train,file=paste(OUT_DIR,"tcdd_dose_detail_vec_train10vs0_time_course.Rds",sep=""))

In [18]:
%%R
cv_fold_indices <- caret::createFolds(tcdd_dose_detail.vec.train,
                                      k = N_FOLDS)
print(cv_fold_indices)

$Fold01
[1] 15 23 27 34 44 49 63 65 86

$Fold02
[1]  1  2 12 31 46 57 58 69 85

$Fold03
[1]  8 10 11 16 22 29 30 43 74

$Fold04
[1]  3  6 32 35 41 48 55 60 84

$Fold05
[1]  4 18 36 51 53 61 64 89 90

$Fold06
[1]  9 13 19 25 37 56 71 77 88

$Fold07
[1]  7 14 17 40 52 59 79 82 87

$Fold08
[1] 24 26 38 39 66 68 72 73 80

$Fold09
[1]  5 21 42 47 50 62 70 75 83

$Fold10
[1] 20 28 33 45 54 67 76 78 81



In [19]:
%%R
binary_tcdd_dose_annotations <- unique(tcdd_dose_detail.vec)
print(binary_tcdd_dose_annotations)

[1]  0 10


In [20]:
%%R
full_rxn_pca_results.nls <- list()
rxn_id_2_result_file_idx.nls <- list()

In [21]:
%%R
n_rxns <- length(rxns)
print(n_rxns)
result_idx <- 1
for(rxn_id_idx in seq(1:n_rxns)){
   rxn_id <- rxns[rxn_id_idx]
   rxn_pca <-
      prcomp(t(vst.count.mtx.train[rxn2ensembls.nls[[rxn_id]], ]), scale. = T)
   full_rxn_pca_results.nls[[rxn_id]] <- rxn_pca
   rxn_id_2_result_file_idx.nls[[rxn_id]] <- result_idx
   rxn_pca.nls[[rxn_id]] <-
      rxn_pca$x[, 1] # 1st principal component coordinate within this reaction-space for each sample
   if(mod(rxn_id_idx,100) == 0){
      print(paste("Processed ",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      flush.console()
   }
   if(mod(rxn_id_idx,1000) == 0){
      print(paste("Storing PCA objects containing reactions ",rxn_id_idx-1000,
                  "-",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      saveRDS(full_rxn_pca_results.nls,
              paste(OUT_DIR, "full_rxn_pca_results_nls",rxn_id_idx-1000,
                    "-",rxn_id_idx,"10vs0_time_course.Rds", sep=""))
      full_rxn_pca_results.nls <- list()
      gc()
      result_idx <- result_idx + 1
   }
}

[1] 9825
[1] "Processed 100 of 9825 reactions (1%)..."
[1] "Processed 200 of 9825 reactions (2%)..."
[1] "Processed 300 of 9825 reactions (3.1%)..."
[1] "Processed 400 of 9825 reactions (4.1%)..."
[1] "Processed 500 of 9825 reactions (5.1%)..."
[1] "Processed 600 of 9825 reactions (6.1%)..."
[1] "Processed 700 of 9825 reactions (7.1%)..."
[1] "Processed 800 of 9825 reactions (8.2%)..."
[1] "Processed 900 of 9825 reactions (9.2%)..."
[1] "Processed 1000 of 9825 reactions (10.2%)..."
[1] "Storing PCA objects containing reactions 0-1000 of 9825 reactions (10.2%)..."
[1] "Processed 1100 of 9825 reactions (11.2%)..."
[1] "Processed 1200 of 9825 reactions (12.2%)..."
[1] "Processed 1300 of 9825 reactions (13.2%)..."
[1] "Processed 1400 of 9825 reactions (14.3%)..."
[1] "Processed 1500 of 9825 reactions (15.3%)..."
[1] "Processed 1600 of 9825 reactions (16.3%)..."
[1] "Processed 1700 of 9825 reactions (17.3%)..."
[1] "Processed 1800 of 9825 reactions (18.3%)..."
[1] "Processed 1900 of 9825 re

In [22]:
%%R
# store remaining PCA objects and removing from RAM
saveRDS(rxn_id_2_result_file_idx.nls,
        paste(OUT_DIR,"rxn_id_2_result_file_idx_nls10vs0_time_course.Rds",sep=""))
saveRDS(full_rxn_pca_results.nls,
        paste(OUT_DIR, "full_rxn_pca_results_nls10vs0_time_course.Rds", sep=""))
rm(full_rxn_pca_results.nls)
gc()

           used  (Mb) gc trigger  (Mb) max used  (Mb)
Ncells  6950693 371.3   13075654 698.4 11881756 634.6
Vcells 15907026 121.4   25842636 197.2 25842636 197.2


In [23]:
%%R
# compare informaction content of below files with pca plots or similar
saveRDS(rxn_pca.nls, paste(OUT_DIR, "rxn_pca_nls10vs0_time_course.Rds", sep = ""))
saveRDS(vst.count.mtx.train,
        paste(OUT_DIR, "vst_count_mtx_train10vs0_time_course.Rds", sep = ""))

In [24]:
%%R
for (cv_fold in names(cv_fold_indices)) {
  cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
}

In [25]:
%%R
# print(tissue_annotation)
# print(binary_tcdd_dose_annotations)
# print(paste("Processing tissue annotation:", tissue_annotation))
# print(length(binary_tcdd_dose_detail_vec.test.cv_test_list))
# print(sum(tcdd_dose_detail.vec.train.cv_test == tissue_annotation))
# print(length(rxns))

# binary_tcdd_dose_annotations <- c(0.00, 30.00, 0.01, 0.03, 0.10, 0.30, 1.00, 3.00, 10.00)

formatted_annotations <- format(binary_tcdd_dose_annotations, nsmall = 2)

formatted_annotations <- trimws(formatted_annotations)

binary_tcdd_dose_annotations <- formatted_annotations

print(binary_tcdd_dose_annotations)
for (annotation in binary_tcdd_dose_annotations) {
    print(annotation)
}

[1] "0.00"  "10.00"
[1] "0.00"
[1] "10.00"


In [26]:
%%R
# main loop
for (rxn_id_idx in seq(1:length(rxns))) {
   rxn_id <- rxns[rxn_id_idx]
   ensembl_ids <- rxn2ensembls.nls[[rxn_id]]
   
   mean_misclass_rate <- list()
   sum_ari <- 0

   for (cv_fold in names(cv_fold_indices)) {
      cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
      
      vst.count.mtx.train.cv_train <-
         vst.count.mtx.train[, -cur_cv_fold_indices] # 4/5ths of training features
      vst.count.mtx.train.cv_test <-
         vst.count.mtx.train[, cur_cv_fold_indices] # 1/5th of training features
      
      tcdd_dose_detail.vec.train.cv_train <-
         tcdd_dose_detail.vec.train[-cur_cv_fold_indices] # 4/5ths of training labels
      tcdd_dose_detail.vec.train.cv_test <-
         tcdd_dose_detail.vec.train[cur_cv_fold_indices] # 1/5th of training labels
      
#        print(length(vst.count.mtx.train.cv_train))
#        print(length(gtex_tissue_detail.vec.train.cv_train))
       
      binary_tcdd_dose_detail_vec.test.cv_test_list <- list()
      for (tissue_annotation in binary_tcdd_dose_annotations) {
#          print(tcdd_dose_detail.vec.train.cv_test)
#          print("-------------")
#          print(tissue_annotation)
#          print(binary_tcdd_dose_detail_vec.test.cv_test_list)
         binary_tcdd_dose_detail_vec.test.cv_test_list[[as.character(tissue_annotation)]] <-
            (as.character(tcdd_dose_detail.vec.train.cv_test) == as.character(tissue_annotation))
      }
      
      cv_train.expr_mat <-
         t(vst.count.mtx.train.cv_train[ensembl_ids, ])
      cv_test.expr_mat <-
         t(vst.count.mtx.train.cv_test[ensembl_ids, ])
#        print(dim(cv_train.expr_mat))
#        print(length(gtex_tissue_detail.vec.train.cv_train))
      
      rxn_knn_calls <- class::knn(train = cv_train.expr_mat,
                                  test = cv_test.expr_mat,
                                  cl = tcdd_dose_detail.vec.train.cv_train)
      
      # calculate & store adjusted rand index
      cur_ari <- pdfCluster::adj.rand.index(rxn_knn_calls,
                                            tcdd_dose_detail.vec.train.cv_test)
      sum_ari <- cur_ari + sum_ari
      
      # for each tissue, calculate misclassification rate
      for (tissue_annotation in binary_tcdd_dose_annotations) {
         cur_rxn_knn_calls <- (rxn_knn_calls == tissue_annotation)
            
         # calculate misclassification rate (https://stat.ethz.ch/pipermail/r-help/2011-September/288885.html)
         tab <- table(cur_rxn_knn_calls,
                      binary_tcdd_dose_detail_vec.test.cv_test_list[[tissue_annotation]])
        # print(tab)
         cur_misclass_rate <- 1 - sum(diag(tab)) / sum(tab)
        # print(paste("Misclass rate = 1 - ",sum(diag(tab))," / ",sum(tab)," = ", cur_misclass_rate,"...",sep=""))
         sum_misclass_rate <- cur_misclass_rate
         if (!is.null(mean_misclass_rate[[tissue_annotation]])) {
           sum_misclass_rate <- sum_misclass_rate + mean_misclass_rate[[tissue_annotation]]
         }
         mean_misclass_rate[[tissue_annotation]] <- sum_misclass_rate
      }
   }
   for(tissue_annotation in binary_tcdd_dose_annotations){
      mean_misclass_rate[[tissue_annotation]] <- (mean_misclass_rate[[tissue_annotation]] / N_FOLDS)
   }
   mean_ari <- sum_ari / N_FOLDS
   ecount <- length(ensembl_ids)
   
   rxn_knn_misclass_rate.nls[[rxn_id]] <- mean_misclass_rate
   assign("mean_misclass_rate",NULL,envir = .GlobalEnv)
   
   rxn_knn_ari.nls[[rxn_id]] <- mean_ari
   rxn_knn_ecount.nls[[rxn_id]] <- ecount
   
   count <- count + 1
   if (mod(count, 10) == 0) {
      print(
         paste(
            "Last RXN_ID = ",
            rxn_id,
            ": Last ARI = ",
            mean_ari,
            ": Last ECOUNT = ",
            ecount,
            ": Last Lung MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Lung"]],
            ": Last Uterus MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Uterus"]],
            ". Now ",
            round(1.0 - count / length(rxns),3) * 100,
            "% remaining..."
         )
      )
      flush.console()
   }
}

[1] "Last RXN_ID =  R-MMU-749456 : Last ARI =  1 : Last ECOUNT =  178 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-9021601 : Last ARI =  1 : Last ECOUNT =  24 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-3108203 : Last ARI =  0.904295774647887 : Last ECOUNT =  15 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9838627 : Last ARI =  0.693184663536776 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-193679 : Last ARI =  0.321608264042084 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-194544 : Last ARI =  -0.0448026779422128 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-3247837 : Las

[1] "Last RXN_ID =  R-MMU-450580 : Last ARI =  0.955555555555555 : Last ECOUNT =  12 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-6791222 : Last ARI =  1 : Last ECOUNT =  61 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9696268 : Last ARI =  1 : Last ECOUNT =  41 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-1912394 : Last ARI =  1 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-8936481 : Last ARI =  0.949295774647887 : Last ECOUNT =  77 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-9677051 : Last ARI =  1 : Last ECOUNT =  10 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-5336403 : Last ARI =  0.804851330203443 : La

[1] "Last RXN_ID =  R-MMU-983156 : Last ARI =  1 : Last ECOUNT =  242 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-174119 : Last ARI =  0.949295774647887 : Last ECOUNT =  18 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-174224 : Last ARI =  0.904851330203443 : Last ECOUNT =  18 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-3788708 : Last ARI =  1 : Last ECOUNT =  23 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-927830 : Last ARI =  1 : Last ECOUNT =  11 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-448955 : Last ARI =  0.955 : Last ECOUNT =  6 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89 % remaining..."
[1] "Last RXN_ID =  R-MMU-200652 : Last ARI =  0.0905665859898118 : Las

[1] "Last RXN_ID =  R-MMU-9013004 : Last ARI =  0.955555555555555 : Last ECOUNT =  16 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-9818576 : Last ARI =  0.165501613796201 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84 % remaining..."
[1] "Last RXN_ID =  R-MMU-2029273 : Last ARI =  1 : Last ECOUNT =  71 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  83.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-8850356 : Last ARI =  0.649295774647887 : Last ECOUNT =  11 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  83.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-1363303 : Last ARI =  0.765258215962441 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  83.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-188386 : Last ARI =  0.43773883611748 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  83.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-3

[1] "Last RXN_ID =  R-NUL-9625422 : Last ARI =  0.460734635083227 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79 % remaining..."
[1] "Last RXN_ID =  R-MMU-1449633 : Last ARI =  0.643998617025148 : Last ECOUNT =  5 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-211910 : Last ARI =  1 : Last ECOUNT =  12 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-3928646 : Last ARI =  1 : Last ECOUNT =  12 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-8848484 : Last ARI =  0.771517996870109 : Last ECOUNT =  5 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9022185 : Last ARI =  0.409702660406886 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-2032396 : Last AR

...

[1] "Last RXN_ID =  R-MMU-73792 : Last ARI =  0.0787888713535618 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  23.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-198275 : Last ARI =  0.425710524556613 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  23 % remaining..."
[1] "Last RXN_ID =  R-MMU-114683 : Last ARI =  0.4113440745483 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-75090 : Last ARI =  -0.0942689718722773 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-77342 : Last ARI =  0.50914710485133 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-449937 : Last ARI =  0.01635932579267 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.5 % remaining..."
[1] "Last RXN_ID =  R-

[1] "Last RXN_ID =  R-MMU-139854 : Last ARI =  0.744444444444444 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  18 % remaining..."
[1] "Last RXN_ID =  R-MMU-198983 : Last ARI =  0.551785993740219 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.9 % remaining..."
[1] "Last RXN_ID =  R-NUL-2128982 : Last ARI =  0.198047353734186 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-9757010 : Last ARI =  1 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9653592 : Last ARI =  0.0226327438011383 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9668464 : Last ARI =  0.0570491719402627 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-24

[1] "Last RXN_ID =  R-MMU-9654054 : Last ARI =  0.407528706374795 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  13 % remaining..."
[1] "Last RXN_ID =  R-MMU-6799545 : Last ARI =  0.252090073761183 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-76386 : Last ARI =  1 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-9012036 : Last ARI =  -0.0477601185793109 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-975633 : Last ARI =  0.511311278523856 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9027532 : Last ARI =  0.301296200594096 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-917

[1] "Last RXN_ID =  R-MMU-8986307 : Last ARI =  0.379419191919192 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  8 % remaining..."
[1] "Last RXN_ID =  R-NUL-844613 : Last ARI =  -0.0350182419820126 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-9629360 : Last ARI =  0.211695939082935 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-6809624 : Last ARI =  0.126940714051752 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-192312 : Last ARI =  0.4875 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-8879117 : Last ARI =  0.16795515394913 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-1399

[1] "Last RXN_ID =  R-MMU-9603983 : Last ARI =  0.388888888888889 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-111883 : Last ARI =  0.154010495525063 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-9622513 : Last ARI =  -0.0270623875565588 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-5661125 : Last ARI =  0.622739018087855 : Last ECOUNT =  14 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9695949 : Last ARI =  -0.0313796922951852 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-1855172 : Last ARI =  -0.00213073606797538 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2.4 % remaining..."
[1] "Last

In [27]:
%%R
saveRDS(
   rxn_knn_misclass_rate.nls,
   paste(OUT_DIR, "toi_rxn_knn_misclass_rate_nls10vs0_time_course.Rds", sep = "")
)
saveRDS(rxn_knn_ari.nls,
        paste(OUT_DIR, "toi_rxn_knn_ari_nls10vs0_time_course.Rds", sep = ""))
saveRDS(rxn_knn_ecount.nls,
        paste(OUT_DIR, "toi_rxn_knn_ecount_nls10vs0_time_course.Rds", sep = ""))

In [28]:
%%R
d <- data.frame(
   RXN_ID = names(rxn2ensembls.nls),
   MISCLASS = unlist(rxn_knn_misclass_rate.nls),
   ARI = unlist(rxn_knn_ari.nls),
   ECOUNT = unlist(rxn_knn_ecount.nls)
)
print(d)
saveRDS(d, paste(OUT_DIR, "toi_summary_df10vs0_time_course.Rds", sep = ""))

                           RXN_ID MISCLASS           ARI ECOUNT
R-MMU-170666.0.00    R-MMU-170666        0  0.9492957746     14
R-MMU-170666.10.00   R-MMU-170671        0  0.9492957746     14
R-MMU-170671.0.00    R-MMU-170674        0  0.9492957746     14
R-MMU-170671.10.00   R-MMU-170686        0  0.9492957746     14
R-MMU-170674.0.00    R-MMU-380073        0  1.0000000000    182
R-MMU-170674.10.00   R-MMU-392187        0  0.9555555556     22
R-MMU-170686.0.00    R-MMU-392195        0  0.9555555556     22
R-MMU-170686.10.00   R-MMU-392202        0  0.9555555556     22
R-MMU-380073.0.00    R-MMU-749454        0  1.0000000000    178
R-MMU-380073.10.00   R-MMU-749456        0  1.0000000000    178
R-MMU-392187.0.00    R-MMU-751001        0  1.0000000000     21
R-MMU-392187.10.00  R-MMU-8964229        0  1.0000000000      5
R-MMU-392195.0.00   R-MMU-8964242        0  1.0000000000      5
R-MMU-392195.10.00  R-MMU-8964329        0  1.0000000000      5
R-MMU-392202.0.00   R-MMU-8982012       

R-MMU-205099.10.00  R-MMU-5654224        0  1.0000000000     12
R-MMU-205112.0.00   R-MMU-5654392        0  1.0000000000     20
R-MMU-205112.10.00  R-MMU-5654397        0  1.0000000000     16
R-MMU-205117.0.00   R-MMU-5654399        0  1.0000000000     16
R-MMU-205117.10.00  R-MMU-5654402        0  1.0000000000     20
R-MMU-209532.0.00   R-MMU-5654404        0  1.0000000000     16
R-MMU-209532.10.00  R-MMU-5654406        0  1.0000000000     18
R-MMU-209566.0.00   R-MMU-5654407        0  1.0000000000     16
R-MMU-209566.10.00  R-MMU-5654408        0  1.0000000000     12
R-MMU-9012761.0.00  R-MMU-5654409        0  1.0000000000     12
R-MMU-9012761.10.00 R-MMU-5654413        0  1.0000000000     17
R-MMU-3247837.0.00  R-MMU-5654416        0  1.0000000000     15
R-MMU-3247837.10.00 R-MMU-5654418        0  1.0000000000     14
R-MMU-3247840.0.00  R-MMU-5654422        0  1.0000000000     14
R-MMU-3247840.10.00 R-MMU-5654423        0  1.0000000000     16
R-MMU-3247843.0.00  R-MMU-5654425       

R-MMU-5654224.10.00 R-MMU-9011082        0  0.4338444688      2
R-MMU-5654392.0.00  R-MMU-9011144        0  0.2717613947      3
R-MMU-5654392.10.00 R-MMU-9011146        0  0.2717613947      3
R-MMU-5654397.0.00  R-MMU-9753028        0  0.8159624413      5
R-MMU-5654397.10.00 R-MMU-9753126        0  0.8159624413      5
R-MMU-5654399.0.00   R-MMU-514604        0  0.0103796902      2
R-MMU-5654399.10.00  R-MMU-975389        0  0.2901888604      4
R-MMU-5654402.0.00  R-MMU-1169394        0  1.0000000000      5
R-MMU-5654402.10.00 R-MMU-1169398        0  0.6270735524      5
R-MMU-5654404.0.00  R-MMU-1169402        0  0.6709624413      6
R-MMU-5654404.10.00 R-MMU-1169403        0  0.5319444444      4
R-MMU-5654406.0.00  R-MMU-1169405        0  0.8159624413      5
R-MMU-5654406.10.00 R-MMU-1169406        0  1.0000000000     12
R-MMU-5654407.0.00  R-MMU-1678842        0  1.0000000000     13
R-MMU-5654407.10.00 R-MMU-1678843        0  0.7715179969      5
R-MMU-5654408.0.00  R-MMU-5653754       

R-MMU-5654659.10.00 R-MMU-2424487        0  1.0000000000     22
R-MMU-5654662.0.00   R-MMU-388814        0  0.6812206573      6
R-MMU-5654662.10.00  R-MMU-388829        0  1.0000000000      9
R-MMU-5654663.0.00   R-MMU-388831        0  1.0000000000      8
R-MMU-5654663.10.00  R-MMU-388832        0  1.0000000000      9
R-MMU-5654664.0.00   R-MMU-388833        0  1.0000000000     17
R-MMU-5654664.10.00  R-MMU-389158        0  1.0000000000      9
R-MMU-5654667.0.00   R-MMU-389348        0  0.6478873239      8
R-MMU-5654667.10.00  R-MMU-389350        0  0.7589984351      8
R-MMU-5654669.0.00   R-MMU-389352        0  0.6478873239      7
R-MMU-5654669.10.00  R-MMU-389354        0  0.6478873239      7
R-MMU-5654672.0.00   R-MMU-389381        0  0.6212990459      6
R-MMU-5654672.10.00  R-MMU-389758        0  0.8733921602     22
R-MMU-5654673.0.00   R-MMU-389759        0  0.7280361757      7
R-MMU-5654673.10.00  R-MMU-389762        0  0.7217763948      5
R-MMU-5654677.0.00   R-MMU-434836       

R-MMU-9011082.10.00 R-MMU-9692139        0  0.2025417657      2
R-MMU-9011144.0.00  R-MMU-9692145        0  0.5101388889      2
R-MMU-9011144.10.00 R-MMU-9692156        0  0.1106990427      4
R-MMU-9011146.0.00  R-MMU-9692157        0  0.1106990427      4
R-MMU-9011146.10.00 R-MMU-9692268        0  0.2161626087      2
R-MMU-9753028.0.00   R-MMU-450434        0  0.0986789198      1
R-MMU-9753028.10.00  R-MMU-450466        0  1.0000000000     45
R-MMU-9753126.0.00   R-MMU-450551        0  0.9111111111      7
R-MMU-9753126.10.00  R-MMU-450580        0  0.9555555556     12
R-MMU-514604.0.00     R-MMU-72103        0  0.9555555556     43
R-MMU-514604.10.00  R-MMU-9770119        0  0.9555555556     69
R-MMU-975389.0.00   R-MMU-9770141        0  1.0000000000    123
R-MMU-975389.10.00  R-MMU-9770142        0  1.0000000000    132
R-MMU-1169394.0.00  R-MMU-9770145        0  1.0000000000    145
R-MMU-1169394.10.00 R-MMU-9770236        0  1.0000000000    119
R-MMU-1169398.0.00  R-MMU-6798748       

...


R-MMU-8849638.0.00  R-MMU-9617657        0  0.1763693271      1
R-MMU-8849638.10.00 R-MMU-9617711        0  0.1763693271      1
R-MMU-8849646.0.00  R-MMU-9617755        0  0.1763693271      1
R-MMU-8849646.10.00 R-NUL-9617710        0  0.1763693271      1
R-MMU-1362465.0.00  R-NUL-9617742        0  0.1763693271      1
R-MMU-1362465.10.00 R-NUL-9617757        0  0.1763693271      1
R-MMU-112435.0.00   R-NUL-9617903        0  0.1763693271      1
R-MMU-112435.10.00  R-NUL-9617912        0  0.1763693271      1
R-MMU-9036987.0.00   R-MMU-187246        0  0.1450181474      2
R-MMU-9036987.10.00  R-MMU-189119        0  0.1450181474      2
R-MMU-9603982.0.00   R-MMU-391942        0  0.0510977267      1
R-MMU-9603982.10.00 R-MMU-9726949        0  0.0510977267      1
R-MMU-9603983.0.00  R-MMU-1564169        0 -0.0432887955      3
R-MMU-9603983.10.00 R-MMU-1602473        0  0.4497835498      1
R-MMU-168412.0.00    R-MMU-389424        0  0.2148865415      1
R-MMU-168412.10.00  R-MMU-9014672      

R-MMU-8985201.0.00  R-MMU-5340195        0  0.0978015348      1
R-MMU-8985201.10.00 R-MMU-6806674        0  0.0054602692      1
R-MMU-196402.0.00    R-MMU-190681        0  0.1999334898      1
R-MMU-196402.10.00  R-MMU-9846477        0  0.0867264191      1
R-MMU-6807055.0.00  R-MMU-8850846        0  0.4256651017      1
R-MMU-6807055.10.00 R-MMU-8850854        0  0.4256651017      1
R-MMU-9816403.0.00  R-MMU-8954468        0  0.3633972510      1
R-MMU-9816403.10.00   R-MMU-70542        0  0.1120816600      1
R-MMU-9816449.0.00  R-MMU-6804402        0  0.2489997549      2
R-MMU-9816449.10.00  R-MMU-418172        0  0.4528971049      2
R-MMU-8849857.0.00  R-MMU-9708866        0  0.2554458062      1
R-MMU-8849857.10.00 R-MMU-9006144        0  0.1597891566      1
R-MMU-1461971.0.00  R-MMU-5336430        0  0.2263512671      2
R-MMU-1461971.10.00 R-MMU-5687126        0  0.0145735524      1
R-MMU-1461982.0.00  R-MMU-9624527        0  0.0145735524      1
R-MMU-1461982.10.00 R-MMU-9699581       

R-MMU-8987120.0.00  R-MMU-9708104        0  0.0823376865      1
R-MMU-8987120.10.00 R-MMU-5688294        0  0.6230331484      3
R-MMU-8937442.0.00  R-MMU-8850797        0  0.4048513302      1
R-MMU-8937442.10.00  R-MMU-444204        0  0.1012702477      1
R-MMU-1254376.0.00  R-MMU-9842656        0  0.7541471049      3
R-MMU-1254376.10.00 R-MMU-9011343        0  0.2368181605      1
R-MMU-211923.0.00   R-MMU-9816416        0  0.4555555556      1
R-MMU-211923.10.00  R-MMU-9820700        0  0.4362108769      4
R-MMU-189423.0.00   R-MMU-1296035        0  0.2930179337      1
R-MMU-189423.10.00  R-MMU-9013021        0  0.1302387037      2
R-MMU-6786421.0.00  R-MMU-9690494        0  0.0847526325      1
R-MMU-6786421.10.00 R-NUL-4649029        0  0.4367762128      1
R-MMU-109341.0.00   R-MMU-1482861        0  0.0017450959      1
R-MMU-109341.10.00  R-MMU-1482867        0  0.0017450959      1
R-MMU-77338.0.00    R-MMU-9663768        0  0.0977145466      1
R-MMU-77338.10.00   R-MMU-9749977       

R-MMU-399978.0.00   R-MMU-3222128        0  0.1479315684      2
R-MMU-399978.10.00  R-MMU-6793685        0 -0.0043622848      1
R-MMU-844438.0.00   R-MMU-6804425        0 -0.0043622848      1
R-MMU-844438.10.00  R-MMU-6804762        0 -0.0043622848      1
R-MMU-844447.0.00   R-MMU-8952128        0  0.0595214190      2
R-MMU-844447.10.00   R-MMU-191303        0  0.8541471049      1
R-MMU-879222.0.00    R-MMU-191322        0  0.8541471049      1
R-MMU-879222.10.00  R-MMU-9717841        0  0.8541471049      1
R-MMU-75823.0.00     R-NUL-421687        0  0.3150613276      1
R-MMU-75823.10.00    R-NUL-421695        0  0.3150613276      1
R-MMU-8952399.0.00  R-MMU-2730846        0  0.4351068828      1
R-MMU-8952399.10.00 R-MMU-2730869        0  0.4351068828      1
R-MMU-176588.0.00   R-MMU-9604768        0  0.4067254935      2
R-MMU-176588.10.00  R-MMU-9606621        0  0.4067254935      2
R-MMU-176604.0.00   R-MMU-9606623        0  0.4067254935      2
R-MMU-176604.10.00  R-MMU-1482973       

R-MMU-5619427.0.00  R-MMU-8874705        0  0.2607915463      1
R-MMU-5619427.10.00 R-MMU-8874718        0  0.2607915463      1
R-MMU-1605723.0.00  R-MMU-8869603        0  0.1123066978      1
R-MMU-1605723.10.00  R-MMU-977317        0  0.1492957746      1
R-MMU-4085029.0.00  R-MMU-2160492        0  0.0728305952      1
R-MMU-4085029.10.00 R-MMU-2162078        0  0.1281042078      1
R-MMU-8878787.0.00   R-MMU-188979        0  0.3111111111      4
R-MMU-8878787.10.00  R-MMU-191114        0  0.3111111111      4
R-MMU-162821.0.00    R-MMU-202717        0  0.2476501007      1
R-MMU-162821.10.00  R-MMU-6807229        0  0.0080139808      1
R-MMU-5619433.0.00  R-MMU-9832829        0  0.3048513302      2
R-MMU-5619433.10.00 R-MMU-2509827        0 -0.0459403107      1
R-MMU-6799977.0.00  R-MMU-2509831        0 -0.0459403107      1
R-MMU-6799977.10.00 R-MMU-2509838        0 -0.0459403107      1
R-MMU-6799981.0.00  R-MMU-9755030        0 -0.0459403107      1
R-MMU-6799981.10.00  R-MMU-351222       

In [29]:
%%R
pid <- read.table(paste(OUT_DIR,"tcdd_project_id10vs0_time_course.txt",sep=""),header=FALSE)
sid <- read.table(paste(OUT_DIR,"tcdd_sample_id10vs0_time_course.txt",sep=""), header=FALSE)
sex <- read.table(paste(OUT_DIR, "tcdd_gender10vs0_time_course.txt", sep=""), header=FALSE)
print(sex)

       V1
1    male
2    male
3    male
4    male
5    male
6    male
7    male
8    male
9    male
10   male
11   male
12   male
13   male
14   male
15   male
16   male
17   male
18   male
19   male
20   male
21   male
22   male
23   male
24   male
25   male
26   male
27   male
28   male
29   male
30   male
31   male
32   male
33   male
34   male
35   male
36   male
37   male
38   male
39   male
40   male
41   male
42   male
43   male
44   male
45   male
46   male
47   male
48   male
49 female
50 female
51 female
52 female
53 female
54 female
55 female
56 female
57 female
58 female
59 female
60 female
61 female
62 female
63 female
64 female
65 female
66 female
67 female
68 female
69 female
70 female
71 female
72 female
73 female
74 female
75 female
76 female
77 female
78 female
79   male
80   male
81   male
82   male
83   male
84   male
85   male
86   male
87   male
88   male
89   male
90   male


In [30]:
%%R
library(htmlwidgets)
min_misclass_pca <-
   prcomp(t(vst.count.mtx.train), scale. = T)
pca.d <- data.frame(
   PC1 = min_misclass_pca$x[, 1],
   PC2 = min_misclass_pca$x[, 2],
   PC3 = min_misclass_pca$x[, 3],
   Section = tcdd_dose_detail.vec.train,
   Project_id = pid$V1,
   Sample_id = sid$V1
)

ggplot(pca.d, aes(x = PC1, y = PC2, colour = Section)) +
   geom_point(size = 3) +  # 绘制点，指定点的大小
   geom_text(aes(label = paste(Project_id, Sample_id)), vjust = -1, hjust = 1, size = 2) +  # 添加标签
   scale_colour_manual(values = c("0" = "red", "10" = "green")) +  # 手动指定颜色
   theme_bw()

p <- plot_ly(
   data = pca.d,
   x = ~PC1,
   y = ~PC2,
   z = ~PC3,
   type = "scatter3d",
   mode = "markers",
   marker = list(
     color = as.factor(pca.d$Section),  # 将 Section 转换为因子
     colors = c("red", "green"),  # 定义颜色
     size = 5
   ),
   text = ~paste("Project ID:", Project_id, "Sample ID:", Sample_id)  # 在悬停文本中显示 Project ID
)
saveWidget(p, "plotly_chart10vs0_time_course.html", selfcontained = TRUE)